In [1]:
import mlatom as ml

In [2]:
# Get the initial guess for the molecules to optimize
initmol = ml.data.molecule.from_xyz_string('''    9

    C            -1.2121068029534          -0.2252488537660           0.0000164117920
    H            -1.2701429633537          -0.8599818439347          -0.8855315546559
    H            -1.2701264459840          -0.8599834499240           0.8855643352209
    H            -2.0710636368970           0.4504289041619           0.0000252076803
    C             0.0804149514179           0.5556635798575           0.0000041512523
    H             0.1395635927681           1.1970970820212          -0.8856250576131
    H             0.1395848675981           1.1970854779804           0.8856411245403
    O             1.1428329343502          -0.3971737931938          -0.0000106635278
    H             1.9796722202817           0.0702558186994          -0.0001121252171''')

In [3]:
# Choose one of the predifined (automatically recognized) methods
mymodel = ml.models.methods(method='ANI-1ccx')

/mlatom/software/miniconda3/lib/python3.11/site-packages/torchani/resources/
/mlatom/software/miniconda3/lib/python3.11/site-packages/torchani/resources/


In [4]:
# Optimize the geometry with the choosen optimizer:
geomopt = ml.optimize_geometry(model=mymodel, initial_molecule=initmol, program='ASE', maximum_number_of_steps=10000)

# Get the optimized molecule
final_mol = geomopt.optimized_molecule
print(final_mol.get_xyz_string())

9

C            -1.2121068000000          -0.2252488500000           0.0000164100000
H            -1.2701429600000          -0.8599818400000          -0.8855315500000
H            -1.2701264500000          -0.8599834500000           0.8855643400000
H            -2.0710636400000           0.4504289000000           0.0000252100000
C             0.0804149500000           0.5556635800000           0.0000041500000
H             0.1395635900000           1.1970970800000          -0.8856250600000
H             0.1395848700000           1.1970854800000           0.8856411200000
O             1.1428329300000          -0.3971737900000          -0.0000106600000
H             1.9796722200000           0.0702558200000          -0.0001121300000



In [5]:
# Do vibration analysis and thermochemistry calculation
freq = ml.thermochemistry(model=mymodel, molecule=final_mol, program='PySCF')
# or vibration analysis only
# freq = ml.freq(model=mymodel, molecule=final_mol, program='')

In [6]:
# Save the molecule with vibration analysis and thermochemistry results
final_mol.dump(filename='molvibr.json',format='json')

In [7]:
# Check vibration analysis
print("Mode     Frequencies     Reduced masses     Force Constants")
print("           (cm^-1)            (AMU)           (mDyne/A)")
for ii in range(len(final_mol.frequencies)):
    print("%d   %13.4f   %13.4f   %13.4f"%(ii,final_mol.frequencies[ii],final_mol.reduced_masses[ii],final_mol.force_constants[ii]))

# Check thermochemistry results
print(f"Zero-point vibrational energy: {final_mol.ZPE} Hartree")
print(f"Enthalpy at 298 K: {final_mol.H} Hartree")
print(f"Gibbs Free energy at 298 K: {final_mol.G} Hartree")
print(f"Heat of formation at 298 K: {final_mol.DeltaHf298} Hartree")

Mode     Frequencies     Reduced masses     Force Constants
           (cm^-1)            (AMU)           (mDyne/A)
0        263.8585          1.0877          0.0446
1        288.6962          1.1303          0.0555
2        429.0266          2.7312          0.2962
3        840.8100          1.0961          0.4566
4        928.7816          2.3273          1.1829
5       1082.9074          3.1819          2.1985
6       1138.4535          1.9665          1.5017
7       1211.4598          1.5473          1.3379
8       1291.7733          1.0696          1.0516
9       1299.3241          1.1131          1.1072
10       1434.5579          1.2319          1.4937
11       1463.8294          1.3261          1.6742
12       1497.2782          1.1422          1.5087
13       1501.9029          1.0458          1.3899
14       1525.2521          1.0541          1.4448
15       3045.0578          1.0532          5.7540
16       3061.5866          1.1131          6.1473
17       3092.6302         

You can compare your results with the output shown above and obtained with the calculations through the input file.

There will be several properties related to thermochemistry listed below that are attributed to the ``molecule`` object (in Hartree for energies and Hartree/K for entropy) after calculation:

In [8]:
saved_dict = {#...
'ZPE': 0.080996,             # Zero-point energy
'DeltaE2U': 0.085241,        # Difference between internal energy and total energy (ZPVE-exclusive)
'DeltaE2H': 0.086185,        # Difference between enthalpy and total energy (ZPVE-exclusive)
'DeltaE2G': 0.055654,        # Difference between Gibbs free energy and total energy (ZPVE-exclusive)
'U0': -154.810964,           # Internal energy at 0 K
'H0': -154.810964,           # Enthalpy at 0 K
'U':  -154.80672,             # Internal energy at 298 K
'H': -154.805775,            # Enthalpy at 298 K
'G': -154.836306,            # Gibbs free energy at 0 K
'S': 0.00010240004758876359, # entropy
'atomization_energy_0K': 1.2120157100000029,
'ZPE_exclusive_atomization_energy_0K': 1.293011710000003,
'DeltaHf298': -0.0903159176864495  # Heat of formation at 298 K
}
# check out dict:
# final_mol.__dict__

You can retrieve the value of the property by directly calling ``molecule.property`` (e.g. ``molecule.G`` will return you the Gibbs free energy of the molecule).

In [9]:
final_mol.G

-154.83632007673512